In [1]:
df = pd.read_csv('/xfs/trades.csv', nrows=1024 * 1024)
df.head()

time  amount  exch     price  server_time side   ticker
0  1531094401700852527  0.0801  bits 6706.6001            0   na  btc_usd
1  1531094401780298519  0.0284  bits 6706.6099            0   na  btc_usd
2  1531094402305708472  0.0050  btfx 6707.0000            0   na  btc_usd
3  1531094403455657797  0.0050  btfx 6706.7002            0   na  btc_usd
4  1531094403592663872  0.0658  btfx 6705.8999            0   na  btc_usd

In [2]:
df.index = pd.to_datetime(df['time'], utc=True)
df.head()

time  amount  exch  \
time                                                                     
2018-07-09 00:00:01.700852527+00:00  1531094401700852527  0.0801  bits   
2018-07-09 00:00:01.780298519+00:00  1531094401780298519  0.0284  bits   
2018-07-09 00:00:02.305708472+00:00  1531094402305708472  0.0050  btfx   
2018-07-09 00:00:03.455657797+00:00  1531094403455657797  0.0050  btfx   
2018-07-09 00:00:03.592663872+00:00  1531094403592663872  0.0658  btfx   

                                        price  server_time side   ticker  
time                                                                      
2018-07-09 00:00:01.700852527+00:00 6706.6001            0   na  btc_usd  
2018-07-09 00:00:01.780298519+00:00 6706.6099            0   na  btc_usd  
2018-07-09 00:00:02.305708472+00:00 6707.0000            0   na  btc_usd  
2018-07-09 00:00:03.455657797+00:00 6706.7002            0   na  btc_usd  
2018-07-09 00:00:03.592663872+00:00 6705.8999            0   na  btc_usd

In [3]:
df.index[0], df.index[-1], df.index[-1] - df.index[0]

(Timestamp('2018-07-09 00:00:01.700852527+0000', tz='UTC'),
 Timestamp('2018-07-11 19:27:34.453569864+0000', tz='UTC'),
 Timedelta('2 days 19:27:32.752717'))

In [4]:
start = "2018-07-10T04:00:00Z" # <- randomly selected start/end 
end   = "2018-07-10T05:00:00Z" #    important point is, 1h span

target_hr = (df.index >= start) & (df.index < end)
assert target_hr.sum() > 0

of_btcusd = df['ticker'] == 'btc_usd'
assert of_btcusd.sum() > 0

of_bmex = df['exch'] == 'bmex'
of_gdax = df['exch'] == 'gdax'

assert of_bmex.sum() > 0
assert of_gdax.sum() > 0

bmex_hr = df.loc[target_hr & of_bmex & of_btcusd, ['price', 'amount']]
gdax_hr = df.loc[target_hr & of_gdax & of_btcusd, ['price', 'amount']]

bmex_size_wt_price = (
    (bmex_hr['price'] * bmex_hr['amount']).sum()
    / bmex_hr['amount'].sum()
)

gdax_size_wt_price = (
    (gdax_hr['price'] * gdax_hr['amount']).sum()
    / gdax_hr['amount'].sum()
)

ratio = bmex_size_wt_price / gdax_size_wt_price # <- final answer (for start,end hr at least)
ratio

1.000578250137079

In [5]:
bmex_hr.shape, gdax_hr.shape

((2714, 2), (1305, 2))

In [6]:
bmex_size_wt_price, gdax_size_wt_price

(6642.42451802828, 6638.585754905495)